In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

%matplotlib inline

import warnings
warnings.filterwarnings("ignore")

In [2]:
def read_csv(df):
    return pd.read_csv(df)

In [3]:
train = read_csv("Intermediate_train.csv")
test = read_csv("Intermediate_test.csv")
policy = read_csv("Intermediate_policies.csv")

In [4]:
(policy.shape,train.shape,test.shape)

((30371, 10), (9376, 15), (4019, 14))

### EDA

In [5]:
policy.head(3)

policy_number product_code               trans_date  \
0  pol000006995    prod00033  2017-07-01 08:24:55.800   
1  pol000009828    prod00005  2017-07-01 09:04:02.217   
2  pol000009828    prod00005  2017-07-01 09:04:02.217   

                 from_date                  to_date    agent  \
0  2017-07-01 00:00:00.000  2018-07-01 00:00:00.000  ag00005   
1  2017-07-03 00:00:00.000  2017-11-02 00:00:00.000  ag00226   
2  2017-07-03 00:00:00.000  2017-11-02 00:00:00.000  ag00226   

  class_of_business client_type renewal_frequency   branch  
0          cob00035      ct0001            rf0002  br00002  
1          cob00009      ct0003            rf0001  br00006  
2          cob00031      ct0003            rf0001  br00006

In [6]:
policy["class_of_business"].unique()

array(['cob00035', 'cob00009', 'cob00031', 'cob00027', 'cob00026',
       'cob00034', 'cob00016', 'cob00023', 'cob00004', 'cob00001',
       'cob00021', 'cob00011', 'cob00037', 'cob00022', 'cob00003',
       'cob00036', 'cob00029', 'cob00002', 'cob00013', 'cob00012',
       'cob00006', 'cob00008', 'cob00030', 'cob00005', 'cob00018',
       'cob00020', 'cob00017', nan, 'cob00015', 'cob00024', 'cob00033',
       'cob00010', 'cob00028', 'cob00038', 'cob00019', 'cob00007',
       'cob00025', 'cob00014'], dtype=object)

In [7]:
policy.isna().sum()

policy_number         0
product_code          0
trans_date            0
from_date             0
to_date               0
agent                 0
class_of_business    46
client_type           0
renewal_frequency     0
branch                0
dtype: int64

In [8]:
policy["class_of_business"].mode()

0    cob00031
dtype: object

In [9]:
policy["class_of_business"].fillna("cob00031",inplace = True)

In [10]:
policy.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 30371 entries, 0 to 30370
Data columns (total 10 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   policy_number      30371 non-null  object
 1   product_code       30371 non-null  object
 2   trans_date         30371 non-null  object
 3   from_date          30371 non-null  object
 4   to_date            30371 non-null  object
 5   agent              30371 non-null  object
 6   class_of_business  30371 non-null  object
 7   client_type        30371 non-null  object
 8   renewal_frequency  30371 non-null  object
 9   branch             30371 non-null  object
dtypes: object(10)
memory usage: 2.3+ MB


In [11]:
policy.isna().sum()

policy_number        0
product_code         0
trans_date           0
from_date            0
to_date              0
agent                0
class_of_business    0
client_type          0
renewal_frequency    0
branch               0
dtype: int64

In [12]:
policy["diff_days"] = (pd.to_datetime(policy["to_date"]) - pd.to_datetime(policy["from_date"])).dt.days

In [13]:
len(policy["policy_number"].unique())

5217

In [14]:
policy.columns

Index(['policy_number', 'product_code', 'trans_date', 'from_date', 'to_date',
       'agent', 'class_of_business', 'client_type', 'renewal_frequency',
       'branch', 'diff_days'],
      dtype='object')

In [15]:
len(policy["branch"].unique())

11

In [16]:
new_cols = policy.groupby("policy_number").agg(
    prod_min = ("product_code","min"),
    prod_max = ("product_code","max"),
    prod_count = ("product_code","count"),
    
    agent_min = ("agent","min"),
    agent_max = ("agent","max"),
    agent_count = ("agent","count"),
    
    clb_min = ("class_of_business","min"),
    clb_max = ("class_of_business","max"),
    clb_count  = ("class_of_business","count"),
    
    diff_days_min = ("diff_days","min"),
    diff_days_max = ("diff_days","max"),
    diff_days_mean = ("diff_days","mean")
    
).reset_index()

In [17]:
new_cols.head(3)

policy_number   prod_min   prod_max  prod_count agent_min agent_max  \
0  pol000005333  prod00002  prod00002           6   ag00005   ag00006   
1  pol000005334  prod00002  prod00002          27   ag00006   ag00006   
2  pol000005335  prod00002  prod00002          20   ag00007   ag00007   

   agent_count   clb_min   clb_max  clb_count  diff_days_min  diff_days_max  \
0            6  cob00004  cob00004          6             79            365   
1           27  cob00001  cob00006         27             30            182   
2           20  cob00001  cob00004         20             41            122   

   diff_days_mean  
0      215.333333  
1      118.407407  
2      112.800000

In [18]:
policy_cat = ["prod_max","agent_min", "prod_min","agent_max","clb_min","clb_max"]

In [19]:
from sklearn.preprocessing import LabelEncoder

In [20]:
encoder = LabelEncoder()

In [21]:
for i in policy_cat:
    new_cols[i] = encoder.fit_transform(new_cols[i])

In [22]:
df = pd.concat([train, test])

In [23]:
df.head(3)

claim_id policy_number  claim_number  sum_insured    product  \
0  ID_JZ7QWRHH57RO  pol000009680  claim0011359     300000.0  prod00027   
1  ID_KQ5TJMVLJ4EP  pol000006869  claim0005272      16000.0  prod00005   
2  ID_NYHI7WJGGIAE  pol000006135  claim0004147       3000.0  prod00029   

     agent class_of_business risk_type   loss_date client_type  \
0  ag00068          cob00031   rt00006  2021-05-13      ct0003   
1  ag00226          cob00010   rt00032  2018-05-13      ct0003   
2  ag00037          cob00010   rt00026  2018-08-18      ct0003   

  renewal_frequency primary_cause secondary_cause   branch    target  
0            rf0001        pc0007         sc00022  br00006  82150.00  
1            rf0001        pc0007         sc00023  br00002   3780.24  
2            rf0001        pc0007         sc00024  br00002   2196.50

In [24]:
len(df["product"].unique())

37

In [25]:
df["sum_insured_min"] = df.groupby("policy_number")["sum_insured"].transform("min")
df["sum_insured_max"] = df.groupby("policy_number")["sum_insured"].transform("max")
df["sum_insured_count"] = df.groupby("policy_number")["sum_insured"].transform("count")
df["sum_insured_sum"] = df.groupby("policy_number")["sum_insured"].transform("sum")
df["sum_insured_mean"] = df.groupby("policy_number")["sum_insured"].transform("mean")


df["product_count"] = df.groupby("policy_number")["product"].transform("count")
df['product_nunique'] = df.groupby(['policy_number'])['product'].transform('nunique')

In [26]:
cat = ['claim_number','product', 'policy_number', 'agent', 'class_of_business', 'risk_type','client_type', 'renewal_frequency', 'primary_cause', 'secondary_cause',
       'branch']

for i in cat:
    df[i+"_frq"] = df[i].map(df[i].value_counts())

In [27]:
df['year'] = pd.to_datetime(df['loss_date']).dt.year
df["month"] = pd.to_datetime(df["loss_date"]).dt.month
df["day"] = pd.to_datetime(df["loss_date"]).dt.day

In [28]:
new_df = df.merge(new_cols, how='left', on='policy_number')

In [29]:
new_df.head(3)

claim_id policy_number  claim_number  sum_insured    product  \
0  ID_JZ7QWRHH57RO  pol000009680  claim0011359     300000.0  prod00027   
1  ID_KQ5TJMVLJ4EP  pol000006869  claim0005272      16000.0  prod00005   
2  ID_NYHI7WJGGIAE  pol000006135  claim0004147       3000.0  prod00029   

     agent class_of_business risk_type   loss_date client_type  ...  \
0  ag00068          cob00031   rt00006  2021-05-13      ct0003  ...   
1  ag00226          cob00010   rt00032  2018-05-13      ct0003  ...   
2  ag00037          cob00010   rt00026  2018-08-18      ct0003  ...   

  prod_count agent_min agent_max agent_count  clb_min  clb_max  clb_count  \
0        8.0      31.0      31.0         8.0     27.0     25.0        8.0   
1        2.0      10.0      10.0         2.0      7.0     25.0        2.0   
2        2.0      47.0      47.0         2.0     27.0     25.0        2.0   

   diff_days_min  diff_days_max  diff_days_mean  
0          119.0          122.0         120.875  
1          122.0          122.0         122.000  
2          121.0          121.0         121.000  

[3 rows x 48 columns]

In [30]:
cat = ['claim_number','product', 'policy_number', 'agent', 'class_of_business', 'risk_type','client_type', 'renewal_frequency', 'primary_cause', 'secondary_cause',
       'branch']

In [31]:
for i in cat:
    new_df[i] = encoder.fit_transform(new_df[i])

In [32]:
new_df.head(3)

claim_id  policy_number  claim_number  sum_insured  product  agent  \
0  ID_JZ7QWRHH57RO           3881         10480     300000.0       26      4   
1  ID_KQ5TJMVLJ4EP           1381          4908      16000.0        4      7   
2  ID_NYHI7WJGGIAE            761          3968       3000.0       28      1   

   class_of_business  risk_type   loss_date  client_type  ...  prod_count  \
0                 30          5  2021-05-13            2  ...         8.0   
1                  9         31  2018-05-13            2  ...         2.0   
2                  9         25  2018-08-18            2  ...         2.0   

   agent_min  agent_max  agent_count  clb_min  clb_max  clb_count  \
0       31.0       31.0          8.0     27.0     25.0        8.0   
1       10.0       10.0          2.0      7.0     25.0        2.0   
2       47.0       47.0          2.0     27.0     25.0        2.0   

   diff_days_min  diff_days_max  diff_days_mean  
0          119.0          122.0         120.875  
1          122.0          122.0         122.000  
2          121.0          121.0         121.000  

[3 rows x 48 columns]

In [33]:
new_test = new_df[new_df["target"].isna()].reset_index()
new_train = new_df[~(new_df["target"].isna())].reset_index()

In [34]:
(new_train.shape,new_test.shape)

((9376, 49), (4019, 49))

In [35]:
(policy.shape,train.shape,test.shape)

((30371, 11), (9376, 15), (4019, 14))

In [36]:
x = new_train.drop(columns=["claim_id","loss_date","index","target"])
y = new_train["target"]

test_df = new_test.drop(columns=["claim_id","loss_date","index","target"])

### baseline model.

In [37]:
from sklearn.model_selection import train_test_split, KFold
import catboost as ctb
from catboost import Pool
from sklearn.metrics import mean_absolute_error

In [38]:
x_train, x_val, y_train, y_val = train_test_split(x,y,test_size = 0.1,random_state = 42)

In [39]:
(x_train.shape,y_train.shape,x_val.shape,y_val.shape)

((8438, 45), (8438,), (938, 45), (938,))

In [40]:
skf = KFold(n_splits=5, random_state=None)

In [41]:
test_score=[]
train_score=[]

In [42]:
for train_index, test_index in skf.split(x_train,y_train):
    #print("TRAIN:", train_index, "TEST:", test_index)
    X_train, X_test = x_train.iloc[train_index], x_train.iloc[test_index]
    Y_train, Y_test = y_train.iloc[train_index], y_train.iloc[test_index]
    
    
    model = ctb.CatBoostRegressor(loss_function="MAE")# 
    train_dataset = Pool(X_train, Y_train, feature_names=list(X_train.columns))
    eval_dataset = Pool(x_val, y_val)
    
    
    model.fit(train_dataset,eval_set=eval_dataset,early_stopping_rounds= 50)
    train_preds = model.predict(X_train)

    
    print("Train MAE score: ",mean_absolute_error(Y_train,train_preds))
    train_score.append(np.mean(mean_absolute_error(Y_train,train_preds)))
   

    test_preds = model.predict(X_test)
    print("Test MAE score: ", mean_absolute_error(Y_test,test_preds))
    test_score.append(np.mean(mean_absolute_error(Y_test,test_preds)))
   

0:	learn: 39115.6855126	test: 44518.5162756	best: 44518.5162756 (0)	total: 225ms	remaining: 3m 45s
1:	learn: 38870.9768471	test: 44299.8619784	best: 44299.8619784 (1)	total: 235ms	remaining: 1m 57s
2:	learn: 38735.5208818	test: 44148.1586784	best: 44148.1586784 (2)	total: 245ms	remaining: 1m 21s
3:	learn: 38625.1909690	test: 44048.9282107	best: 44048.9282107 (3)	total: 252ms	remaining: 1m 2s
4:	learn: 38419.6258527	test: 43849.6029646	best: 43849.6029646 (4)	total: 260ms	remaining: 51.6s
5:	learn: 38285.7478635	test: 43729.6517387	best: 43729.6517387 (5)	total: 266ms	remaining: 44.1s
6:	learn: 38130.5117714	test: 43594.0935056	best: 43594.0935056 (6)	total: 273ms	remaining: 38.8s
7:	learn: 37980.3779587	test: 43473.0108552	best: 43473.0108552 (7)	total: 281ms	remaining: 34.8s
8:	learn: 37832.7715896	test: 43334.5588944	best: 43334.5588944 (8)	total: 287ms	remaining: 31.6s
9:	learn: 37677.8569963	test: 43203.3271487	best: 43203.3271487 (9)	total: 295ms	remaining: 29.2s
10:	learn: 37582.

97:	learn: 34445.0238976	test: 41159.4141035	best: 41159.4141035 (97)	total: 984ms	remaining: 9.05s
98:	learn: 34431.9740104	test: 41144.0360844	best: 41144.0360844 (98)	total: 992ms	remaining: 9.03s
99:	learn: 34428.5720912	test: 41141.0262326	best: 41141.0262326 (99)	total: 1s	remaining: 9.02s
100:	learn: 34427.5848893	test: 41141.0826146	best: 41141.0262326 (99)	total: 1.01s	remaining: 9s
101:	learn: 34426.1113098	test: 41140.2273831	best: 41140.2273831 (101)	total: 1.02s	remaining: 8.97s
102:	learn: 34406.4189030	test: 41137.6725643	best: 41137.6725643 (102)	total: 1.03s	remaining: 8.94s
103:	learn: 34393.0459553	test: 41129.5034562	best: 41129.5034562 (103)	total: 1.03s	remaining: 8.91s
104:	learn: 34392.2342723	test: 41128.5713478	best: 41128.5713478 (104)	total: 1.04s	remaining: 8.88s
105:	learn: 34390.5233335	test: 41129.0509609	best: 41128.5713478 (104)	total: 1.05s	remaining: 8.84s
106:	learn: 34384.6256053	test: 41127.5383395	best: 41127.5383395 (106)	total: 1.05s	remaining:

201:	learn: 33243.2437526	test: 40604.8803013	best: 40603.6364864 (199)	total: 1.77s	remaining: 7s
202:	learn: 33236.5292202	test: 40603.7112133	best: 40603.6364864 (199)	total: 1.78s	remaining: 6.99s
203:	learn: 33235.6656276	test: 40602.8132195	best: 40602.8132195 (203)	total: 1.79s	remaining: 6.99s
204:	learn: 33231.1419289	test: 40601.3430547	best: 40601.3430547 (204)	total: 1.8s	remaining: 6.98s
205:	learn: 33230.6823819	test: 40601.5689624	best: 40601.3430547 (204)	total: 1.81s	remaining: 6.97s
206:	learn: 33224.2289184	test: 40601.3614095	best: 40601.3430547 (204)	total: 1.81s	remaining: 6.96s
207:	learn: 33203.4184760	test: 40620.2009724	best: 40601.3430547 (204)	total: 1.82s	remaining: 6.94s
208:	learn: 33195.6094841	test: 40625.7300662	best: 40601.3430547 (204)	total: 1.83s	remaining: 6.93s
209:	learn: 33194.5734558	test: 40624.8044409	best: 40601.3430547 (204)	total: 1.84s	remaining: 6.91s
210:	learn: 33180.9670462	test: 40610.8472323	best: 40601.3430547 (204)	total: 1.84s	r

305:	learn: 32474.3251888	test: 40287.1458845	best: 40287.1458845 (305)	total: 2.54s	remaining: 5.77s
306:	learn: 32467.7993088	test: 40293.5252820	best: 40287.1458845 (305)	total: 2.55s	remaining: 5.76s
307:	learn: 32467.1074131	test: 40292.1284929	best: 40287.1458845 (305)	total: 2.56s	remaining: 5.76s
308:	learn: 32456.8856642	test: 40282.6046248	best: 40282.6046248 (308)	total: 2.57s	remaining: 5.75s
309:	learn: 32451.0557693	test: 40277.6443381	best: 40277.6443381 (309)	total: 2.58s	remaining: 5.74s
310:	learn: 32448.1676870	test: 40278.1614607	best: 40277.6443381 (309)	total: 2.58s	remaining: 5.73s
311:	learn: 32447.6330072	test: 40278.0076681	best: 40277.6443381 (309)	total: 2.59s	remaining: 5.72s
312:	learn: 32444.6201997	test: 40280.7026020	best: 40277.6443381 (309)	total: 2.6s	remaining: 5.71s
313:	learn: 32441.7153633	test: 40281.7669044	best: 40277.6443381 (309)	total: 2.61s	remaining: 5.7s
314:	learn: 32433.5780734	test: 40280.9528913	best: 40277.6443381 (309)	total: 2.61s

398:	learn: 31896.1469135	test: 40097.6565642	best: 40096.0095355 (395)	total: 3.28s	remaining: 4.95s
399:	learn: 31888.4056029	test: 40097.2941361	best: 40096.0095355 (395)	total: 3.29s	remaining: 4.94s
400:	learn: 31868.4814217	test: 40069.6554402	best: 40069.6554402 (400)	total: 3.3s	remaining: 4.94s
401:	learn: 31866.8254698	test: 40069.6951596	best: 40069.6554402 (400)	total: 3.31s	remaining: 4.93s
402:	learn: 31858.1329380	test: 40064.4961585	best: 40064.4961585 (402)	total: 3.32s	remaining: 4.92s
403:	learn: 31851.3031573	test: 40064.0517957	best: 40064.0517957 (403)	total: 3.33s	remaining: 4.91s
404:	learn: 31845.9344271	test: 40061.6853924	best: 40061.6853924 (404)	total: 3.33s	remaining: 4.9s
405:	learn: 31827.9199767	test: 40074.3104561	best: 40061.6853924 (404)	total: 3.34s	remaining: 4.89s
406:	learn: 31825.6497970	test: 40074.5593459	best: 40061.6853924 (404)	total: 3.35s	remaining: 4.88s
407:	learn: 31794.9129547	test: 40078.6006710	best: 40061.6853924 (404)	total: 3.36s

...

65:	learn: 35988.6765795	test: 41484.3088341	best: 41484.3088341 (65)	total: 505ms	remaining: 7.14s
66:	learn: 35977.2592444	test: 41477.2012916	best: 41477.2012916 (66)	total: 514ms	remaining: 7.16s
67:	learn: 35975.1068958	test: 41476.9367621	best: 41476.9367621 (67)	total: 527ms	remaining: 7.22s
68:	learn: 35971.2780859	test: 41474.4110492	best: 41474.4110492 (68)	total: 534ms	remaining: 7.21s
69:	learn: 35968.6743791	test: 41472.7467120	best: 41472.7467120 (69)	total: 542ms	remaining: 7.2s
70:	learn: 35949.2170823	test: 41457.8490630	best: 41457.8490630 (70)	total: 550ms	remaining: 7.19s
71:	learn: 35883.9899476	test: 41430.4017654	best: 41430.4017654 (71)	total: 557ms	remaining: 7.18s
72:	learn: 35864.4256241	test: 41418.6190297	best: 41418.6190297 (72)	total: 565ms	remaining: 7.17s
73:	learn: 35822.6179685	test: 41400.6258939	best: 41400.6258939 (73)	total: 572ms	remaining: 7.16s
74:	learn: 35796.6997395	test: 41387.5639743	best: 41387.5639743 (74)	total: 579ms	remaining: 7.14s
7

166:	learn: 34426.2377655	test: 40546.8518912	best: 40546.8518912 (166)	total: 1.28s	remaining: 6.41s
167:	learn: 34383.8291464	test: 40533.2181530	best: 40533.2181530 (167)	total: 1.3s	remaining: 6.43s
168:	learn: 34349.6034361	test: 40540.3721820	best: 40533.2181530 (167)	total: 1.31s	remaining: 6.46s
169:	learn: 34341.0277808	test: 40542.6817944	best: 40533.2181530 (167)	total: 1.32s	remaining: 6.46s
170:	learn: 34314.4138605	test: 40538.7190223	best: 40533.2181530 (167)	total: 1.33s	remaining: 6.45s
171:	learn: 34312.7342417	test: 40536.0567221	best: 40533.2181530 (167)	total: 1.34s	remaining: 6.44s
172:	learn: 34282.6985437	test: 40519.3328456	best: 40519.3328456 (172)	total: 1.34s	remaining: 6.43s
173:	learn: 34278.6441038	test: 40515.0798358	best: 40515.0798358 (173)	total: 1.35s	remaining: 6.42s
174:	learn: 34272.2848626	test: 40509.5011959	best: 40509.5011959 (174)	total: 1.36s	remaining: 6.41s
175:	learn: 34270.0361592	test: 40508.9609650	best: 40508.9609650 (175)	total: 1.37

265:	learn: 33446.4153410	test: 40379.0881611	best: 40379.0881611 (265)	total: 2.06s	remaining: 5.67s
266:	learn: 33443.3955029	test: 40380.3787412	best: 40379.0881611 (265)	total: 2.06s	remaining: 5.67s
267:	learn: 33436.4023312	test: 40376.7982966	best: 40376.7982966 (267)	total: 2.08s	remaining: 5.67s
268:	learn: 33429.6176992	test: 40376.2301827	best: 40376.2301827 (268)	total: 2.08s	remaining: 5.67s
269:	learn: 33425.8265389	test: 40375.9978857	best: 40375.9978857 (269)	total: 2.09s	remaining: 5.66s
270:	learn: 33414.5391814	test: 40373.4888786	best: 40373.4888786 (270)	total: 2.1s	remaining: 5.65s
271:	learn: 33405.9306357	test: 40367.2011171	best: 40367.2011171 (271)	total: 2.11s	remaining: 5.64s
272:	learn: 33403.2532286	test: 40366.0829770	best: 40366.0829770 (272)	total: 2.12s	remaining: 5.63s
273:	learn: 33393.4784917	test: 40362.1807496	best: 40362.1807496 (273)	total: 2.12s	remaining: 5.63s
274:	learn: 33392.4379958	test: 40362.6090343	best: 40362.1807496 (273)	total: 2.13

365:	learn: 32595.3592516	test: 40219.0798309	best: 40218.8144043 (360)	total: 2.81s	remaining: 4.88s
366:	learn: 32591.8876704	test: 40218.2356952	best: 40218.2356952 (366)	total: 2.82s	remaining: 4.87s
367:	learn: 32590.5843177	test: 40218.0196088	best: 40218.0196088 (367)	total: 2.83s	remaining: 4.87s
368:	learn: 32561.1007588	test: 40202.1365717	best: 40202.1365717 (368)	total: 2.84s	remaining: 4.86s
369:	learn: 32554.5324938	test: 40198.8685849	best: 40198.8685849 (369)	total: 2.85s	remaining: 4.85s
370:	learn: 32550.4733481	test: 40197.9125963	best: 40197.9125963 (370)	total: 2.86s	remaining: 4.84s
371:	learn: 32545.8105720	test: 40196.9550582	best: 40196.9550582 (371)	total: 2.86s	remaining: 4.84s
372:	learn: 32544.9595628	test: 40196.6226125	best: 40196.6226125 (372)	total: 2.87s	remaining: 4.83s
373:	learn: 32542.0109934	test: 40193.6254788	best: 40193.6254788 (373)	total: 2.88s	remaining: 4.82s
374:	learn: 32539.0276643	test: 40191.7831115	best: 40191.7831115 (374)	total: 2.8

457:	learn: 31852.4119952	test: 39980.7292230	best: 39980.7292230 (457)	total: 3.54s	remaining: 4.19s
458:	learn: 31849.3101468	test: 39965.7586160	best: 39965.7586160 (458)	total: 3.55s	remaining: 4.18s
459:	learn: 31841.6146039	test: 39964.5010255	best: 39964.5010255 (459)	total: 3.56s	remaining: 4.18s
460:	learn: 31835.4959284	test: 39964.9938231	best: 39964.5010255 (459)	total: 3.57s	remaining: 4.17s
461:	learn: 31830.5694626	test: 39966.2573221	best: 39964.5010255 (459)	total: 3.57s	remaining: 4.16s
462:	learn: 31814.6552120	test: 39966.0552192	best: 39964.5010255 (459)	total: 3.58s	remaining: 4.16s
463:	learn: 31813.6349962	test: 39965.7773062	best: 39964.5010255 (459)	total: 3.59s	remaining: 4.15s
464:	learn: 31800.2266692	test: 40040.7288070	best: 39964.5010255 (459)	total: 3.6s	remaining: 4.14s
465:	learn: 31770.8803288	test: 40184.8083369	best: 39964.5010255 (459)	total: 3.6s	remaining: 4.13s
466:	learn: 31767.5300871	test: 40186.5918660	best: 39964.5010255 (459)	total: 3.61s

In [43]:
print("Training Score: ",np.mean(train_score))
print("Test Score: ",np.mean(test_score))

Training Score:  31720.27372996344
Test Score:  34657.01636271826


In [ ]:
34232.05224623882

### Using GridSearch CV

In [48]:
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_absolute_error,make_scorer

In [54]:
reg = ctb.CatBoostRegressor()

params = {
    "depth": [4,5,6,7,8],
    "l2_leaf_reg": np.logspace(-20,-19,3),
    #"max_depth": [3,4,5,6,7],
    #"colsample_bytree":[],
    #"subsample":[]
}


In [55]:
scorer = make_scorer(mean_absolute_error)
reg_grid = GridSearchCV(estimator=reg,param_grid=params, scoring=scorer,cv=5)

In [56]:
x_train, x_val, y_train, y_val = train_test_split(x,y,test_size = 0.3,random_state = 42)

In [57]:
reg_grid.fit(x_train,y_train)
best_params = reg_grid.best_params_

0:	learn: 203924.6147716	total: 4.37ms	remaining: 4.36s
1:	learn: 202337.4613467	total: 7.87ms	remaining: 3.93s
2:	learn: 201000.8052073	total: 11.3ms	remaining: 3.76s
3:	learn: 199677.2680028	total: 14.8ms	remaining: 3.69s
4:	learn: 198235.4097502	total: 18.2ms	remaining: 3.62s
5:	learn: 196673.3392128	total: 21.5ms	remaining: 3.57s
6:	learn: 195181.8856959	total: 24.7ms	remaining: 3.5s
7:	learn: 194175.3268716	total: 27.9ms	remaining: 3.46s
8:	learn: 192824.8395804	total: 31.4ms	remaining: 3.46s
9:	learn: 191710.6560668	total: 34.8ms	remaining: 3.44s
10:	learn: 190644.3897786	total: 38ms	remaining: 3.42s
11:	learn: 189808.1568109	total: 41.6ms	remaining: 3.42s
12:	learn: 189025.8593244	total: 45.3ms	remaining: 3.44s
13:	learn: 188000.9757079	total: 48.5ms	remaining: 3.42s
14:	learn: 187082.2113145	total: 51.7ms	remaining: 3.4s
15:	learn: 186093.6856008	total: 54.8ms	remaining: 3.37s
16:	learn: 185145.9138067	total: 58.7ms	remaining: 3.39s
17:	learn: 184538.4403811	total: 62ms	remaini

154:	learn: 132777.3510921	total: 533ms	remaining: 2.91s
155:	learn: 132719.0574889	total: 537ms	remaining: 2.91s
156:	learn: 132620.5870550	total: 541ms	remaining: 2.9s
157:	learn: 132207.9555521	total: 545ms	remaining: 2.9s
158:	learn: 132159.7851075	total: 550ms	remaining: 2.91s
159:	learn: 132021.1462843	total: 555ms	remaining: 2.91s
160:	learn: 131759.9958947	total: 562ms	remaining: 2.93s
161:	learn: 131367.3417945	total: 566ms	remaining: 2.93s
162:	learn: 131303.4444898	total: 570ms	remaining: 2.92s
163:	learn: 131197.8484908	total: 574ms	remaining: 2.93s
164:	learn: 131107.2259967	total: 579ms	remaining: 2.93s
165:	learn: 130716.6029940	total: 582ms	remaining: 2.92s
166:	learn: 130628.4507825	total: 586ms	remaining: 2.92s
167:	learn: 130485.5526662	total: 589ms	remaining: 2.92s
168:	learn: 130383.5755500	total: 594ms	remaining: 2.92s
169:	learn: 130305.7455930	total: 597ms	remaining: 2.91s
170:	learn: 130163.5705075	total: 600ms	remaining: 2.91s
171:	learn: 130114.5770731	total:

304:	learn: 116113.2211084	total: 1.07s	remaining: 2.43s
305:	learn: 115878.4427467	total: 1.07s	remaining: 2.43s
306:	learn: 115848.3486304	total: 1.08s	remaining: 2.43s
307:	learn: 115810.9623124	total: 1.08s	remaining: 2.43s
308:	learn: 115531.6652516	total: 1.08s	remaining: 2.43s
309:	learn: 115429.7903798	total: 1.09s	remaining: 2.42s
310:	learn: 115298.3331018	total: 1.1s	remaining: 2.43s
311:	learn: 115251.6492947	total: 1.1s	remaining: 2.43s
312:	learn: 115208.9760008	total: 1.11s	remaining: 2.43s
313:	learn: 115089.4198628	total: 1.11s	remaining: 2.42s
314:	learn: 115034.7098936	total: 1.11s	remaining: 2.42s
315:	learn: 115003.0122968	total: 1.12s	remaining: 2.42s
316:	learn: 114920.7855235	total: 1.12s	remaining: 2.42s
317:	learn: 114881.5770401	total: 1.13s	remaining: 2.41s
318:	learn: 114756.6755350	total: 1.13s	remaining: 2.41s
319:	learn: 114500.9510967	total: 1.13s	remaining: 2.41s
320:	learn: 114395.9385616	total: 1.14s	remaining: 2.41s
321:	learn: 114267.8074047	total:

498:	learn: 101408.3159129	total: 1.78s	remaining: 1.78s
499:	learn: 101192.0181766	total: 1.78s	remaining: 1.78s
500:	learn: 101168.0092083	total: 1.78s	remaining: 1.78s
501:	learn: 101138.4293031	total: 1.79s	remaining: 1.77s
502:	learn: 101099.7140422	total: 1.79s	remaining: 1.77s
503:	learn: 101063.4421043	total: 1.8s	remaining: 1.77s
504:	learn: 101024.2665113	total: 1.8s	remaining: 1.76s
505:	learn: 100989.6480952	total: 1.8s	remaining: 1.76s
506:	learn: 100883.2271470	total: 1.81s	remaining: 1.76s
507:	learn: 100475.0964722	total: 1.81s	remaining: 1.76s
508:	learn: 100447.1126015	total: 1.82s	remaining: 1.75s
509:	learn: 100378.7967918	total: 1.82s	remaining: 1.75s
510:	learn: 100352.8787604	total: 1.83s	remaining: 1.75s
511:	learn: 100315.0730937	total: 1.83s	remaining: 1.74s
512:	learn: 100204.6451757	total: 1.83s	remaining: 1.74s
513:	learn: 100140.1188139	total: 1.84s	remaining: 1.74s
514:	learn: 99753.5594418	total: 1.84s	remaining: 1.74s
515:	learn: 99716.7355481	total: 1.

675:	learn: 90460.1562101	total: 2.47s	remaining: 1.19s
676:	learn: 90410.5054202	total: 2.48s	remaining: 1.18s
677:	learn: 90363.1731943	total: 2.48s	remaining: 1.18s
678:	learn: 90290.7855422	total: 2.49s	remaining: 1.18s
679:	learn: 90266.1271334	total: 2.49s	remaining: 1.17s
680:	learn: 90240.5211878	total: 2.5s	remaining: 1.17s
681:	learn: 90196.2980627	total: 2.5s	remaining: 1.17s
682:	learn: 90154.9882018	total: 2.5s	remaining: 1.16s
683:	learn: 90131.3316486	total: 2.51s	remaining: 1.16s
684:	learn: 90108.7890475	total: 2.51s	remaining: 1.16s
685:	learn: 90094.1711117	total: 2.52s	remaining: 1.15s
686:	learn: 90058.8256798	total: 2.52s	remaining: 1.15s
687:	learn: 89882.1683539	total: 2.52s	remaining: 1.14s
688:	learn: 89874.3843691	total: 2.53s	remaining: 1.14s
689:	learn: 89804.9627981	total: 2.53s	remaining: 1.14s
690:	learn: 89785.3234124	total: 2.53s	remaining: 1.13s
691:	learn: 89757.3469486	total: 2.54s	remaining: 1.13s
692:	learn: 89737.3136008	total: 2.54s	remaining: 1

...

202:	learn: 112128.9233935	total: 1.29s	remaining: 5.08s
203:	learn: 112018.8908308	total: 1.3s	remaining: 5.08s
204:	learn: 111941.7213524	total: 1.31s	remaining: 5.08s
205:	learn: 111886.2753005	total: 1.32s	remaining: 5.08s
206:	learn: 111621.5075896	total: 1.32s	remaining: 5.08s
207:	learn: 111204.1537735	total: 1.33s	remaining: 5.08s
208:	learn: 111163.3971466	total: 1.34s	remaining: 5.08s
209:	learn: 110980.5507712	total: 1.35s	remaining: 5.08s
210:	learn: 110806.5639450	total: 1.36s	remaining: 5.08s
211:	learn: 110777.3095662	total: 1.36s	remaining: 5.07s
212:	learn: 110616.7806209	total: 1.37s	remaining: 5.06s
213:	learn: 110441.0703371	total: 1.38s	remaining: 5.06s
214:	learn: 110353.6183601	total: 1.38s	remaining: 5.05s
215:	learn: 110193.8609710	total: 1.39s	remaining: 5.04s
216:	learn: 109861.9222736	total: 1.39s	remaining: 5.03s
217:	learn: 109748.8306286	total: 1.4s	remaining: 5.02s
218:	learn: 109565.0173333	total: 1.41s	remaining: 5.01s
219:	learn: 109520.3269336	total:

373:	learn: 92550.5863835	total: 2.41s	remaining: 4.04s
374:	learn: 92390.3196662	total: 2.42s	remaining: 4.04s
375:	learn: 92329.7402147	total: 2.43s	remaining: 4.03s
376:	learn: 92249.3972054	total: 2.44s	remaining: 4.03s
377:	learn: 92180.4311796	total: 2.44s	remaining: 4.02s
378:	learn: 92020.4185031	total: 2.45s	remaining: 4.02s
379:	learn: 91966.8827224	total: 2.46s	remaining: 4.01s
380:	learn: 91867.4941477	total: 2.47s	remaining: 4.01s
381:	learn: 91726.5526554	total: 2.48s	remaining: 4.01s
382:	learn: 91602.7482047	total: 2.48s	remaining: 4s
383:	learn: 91520.7594797	total: 2.49s	remaining: 3.99s
384:	learn: 91447.1560917	total: 2.5s	remaining: 3.98s
385:	learn: 91359.4871637	total: 2.5s	remaining: 3.98s
386:	learn: 91293.9713055	total: 2.51s	remaining: 3.97s
387:	learn: 91200.6934716	total: 2.51s	remaining: 3.96s
388:	learn: 91172.5419499	total: 2.52s	remaining: 3.96s
389:	learn: 91132.8630995	total: 2.53s	remaining: 3.95s
390:	learn: 91034.2112738	total: 2.53s	remaining: 3.9

541:	learn: 80342.8595655	total: 3.48s	remaining: 2.94s
542:	learn: 80304.6859295	total: 3.48s	remaining: 2.93s
543:	learn: 80147.8825472	total: 3.49s	remaining: 2.92s
544:	learn: 79974.7769296	total: 3.5s	remaining: 2.92s
545:	learn: 79937.5470603	total: 3.5s	remaining: 2.91s
546:	learn: 79901.4666829	total: 3.51s	remaining: 2.9s
547:	learn: 79865.2098794	total: 3.51s	remaining: 2.9s
548:	learn: 79814.4775664	total: 3.52s	remaining: 2.89s
549:	learn: 79647.4603124	total: 3.53s	remaining: 2.89s
550:	learn: 79603.1175946	total: 3.54s	remaining: 2.89s
551:	learn: 79551.4497662	total: 3.55s	remaining: 2.88s
552:	learn: 79470.4775752	total: 3.56s	remaining: 2.87s
553:	learn: 79433.8368459	total: 3.56s	remaining: 2.87s
554:	learn: 79400.1662271	total: 3.57s	remaining: 2.86s
555:	learn: 79369.8487648	total: 3.57s	remaining: 2.85s
556:	learn: 79261.6321947	total: 3.58s	remaining: 2.85s
557:	learn: 79241.7202332	total: 3.58s	remaining: 2.84s
558:	learn: 79084.5971337	total: 3.59s	remaining: 2.

707:	learn: 71445.0515360	total: 4.56s	remaining: 1.88s
708:	learn: 71405.6469634	total: 4.57s	remaining: 1.87s
709:	learn: 71365.8579042	total: 4.58s	remaining: 1.87s
710:	learn: 71352.3549411	total: 4.58s	remaining: 1.86s
711:	learn: 71314.9174601	total: 4.59s	remaining: 1.86s
712:	learn: 71287.1598171	total: 4.6s	remaining: 1.85s
713:	learn: 71263.8814551	total: 4.61s	remaining: 1.84s
714:	learn: 71209.1202180	total: 4.62s	remaining: 1.84s
715:	learn: 71162.1001152	total: 4.62s	remaining: 1.83s
716:	learn: 71120.4737407	total: 4.63s	remaining: 1.83s
717:	learn: 71098.6298423	total: 4.64s	remaining: 1.82s
718:	learn: 71076.0080229	total: 4.64s	remaining: 1.81s
719:	learn: 71033.1672199	total: 4.65s	remaining: 1.81s
720:	learn: 70998.8361731	total: 4.65s	remaining: 1.8s
721:	learn: 70944.7684671	total: 4.66s	remaining: 1.79s
722:	learn: 70900.1179246	total: 4.67s	remaining: 1.79s
723:	learn: 70848.3738343	total: 4.67s	remaining: 1.78s
724:	learn: 70809.6468435	total: 4.68s	remaining: 

878:	learn: 65098.4115191	total: 5.69s	remaining: 783ms
879:	learn: 65085.0326748	total: 5.7s	remaining: 777ms
880:	learn: 65057.2776546	total: 5.71s	remaining: 771ms
881:	learn: 65035.5961313	total: 5.71s	remaining: 765ms
882:	learn: 65015.5057043	total: 5.72s	remaining: 758ms
883:	learn: 64993.0251476	total: 5.73s	remaining: 752ms
884:	learn: 64963.3473595	total: 5.74s	remaining: 746ms
885:	learn: 64928.6517976	total: 5.75s	remaining: 740ms
886:	learn: 64910.4989466	total: 5.75s	remaining: 733ms
887:	learn: 64879.9814360	total: 5.76s	remaining: 727ms
888:	learn: 64860.5468015	total: 5.77s	remaining: 720ms
889:	learn: 64827.6912974	total: 5.77s	remaining: 714ms
890:	learn: 64807.3028940	total: 5.78s	remaining: 707ms
891:	learn: 64777.4675100	total: 5.79s	remaining: 701ms
892:	learn: 64700.7691422	total: 5.79s	remaining: 694ms
893:	learn: 64681.2243743	total: 5.8s	remaining: 687ms
894:	learn: 64661.9171170	total: 5.8s	remaining: 681ms
895:	learn: 64644.7269773	total: 5.81s	remaining: 6

In [58]:
best_params

{'depth': 5, 'l2_leaf_reg': 1e-20}

### Final Model

In [62]:
test_score=[]
train_score=[]
sub_list = []

In [63]:
for train_index, test_index in skf.split(x_train,y_train):
    #print("TRAIN:", train_index, "TEST:", test_index)
    X_train, X_test = x_train.iloc[train_index], x_train.iloc[test_index]
    Y_train, Y_test = y_train.iloc[train_index], y_train.iloc[test_index]
    
    
    model = ctb.CatBoostRegressor(loss_function="MAE",depth= 5, l2_leaf_reg= 1e-20)# 
    train_dataset = Pool(X_train, Y_train, feature_names=list(X_train.columns))
    eval_dataset = Pool(x_val, y_val)
    
    
    model.fit(train_dataset,eval_set=eval_dataset,early_stopping_rounds= 50)
    train_preds = model.predict(X_train)

    
    print("Train MAE score: ",mean_absolute_error(Y_train,train_preds))
    train_score.append(np.mean(mean_absolute_error(Y_train,train_preds)))
   

    test_preds = model.predict(X_test)
    print("Test MAE score: ", mean_absolute_error(Y_test,test_preds))
    test_score.append(np.mean(mean_absolute_error(Y_test,test_preds)))
   
    submission = model.predict(test_df)
    sub_list.append(submission) 

0:	learn: 41179.5920086	test: 43748.1641753	best: 43748.1641753 (0)	total: 5.9ms	remaining: 5.89s
1:	learn: 40994.7968983	test: 43574.2691726	best: 43574.2691726 (1)	total: 11ms	remaining: 5.5s
2:	learn: 40784.0163058	test: 43361.2463023	best: 43361.2463023 (2)	total: 15.9ms	remaining: 5.29s
3:	learn: 40621.8302388	test: 43205.9804040	best: 43205.9804040 (3)	total: 21ms	remaining: 5.23s
4:	learn: 40427.9227199	test: 43015.2389749	best: 43015.2389749 (4)	total: 25.8ms	remaining: 5.13s
5:	learn: 40305.7126221	test: 42896.5288464	best: 42896.5288464 (5)	total: 30.7ms	remaining: 5.09s
6:	learn: 40190.0748795	test: 42787.8706376	best: 42787.8706376 (6)	total: 36.2ms	remaining: 5.13s
7:	learn: 40097.9144141	test: 42711.2292084	best: 42711.2292084 (7)	total: 41.2ms	remaining: 5.11s
8:	learn: 39942.1323212	test: 42548.4714273	best: 42548.4714273 (8)	total: 46.3ms	remaining: 5.1s
9:	learn: 39775.8275324	test: 42359.7458462	best: 42359.7458462 (9)	total: 51.2ms	remaining: 5.07s
10:	learn: 39641.

105:	learn: 36694.8383526	test: 39785.4315619	best: 39785.4315619 (105)	total: 557ms	remaining: 4.7s
106:	learn: 36691.8694794	test: 39783.1068778	best: 39783.1068778 (106)	total: 563ms	remaining: 4.7s
107:	learn: 36649.3394237	test: 39730.3330285	best: 39730.3330285 (107)	total: 569ms	remaining: 4.7s
108:	learn: 36646.2310187	test: 39730.7607239	best: 39730.3330285 (107)	total: 576ms	remaining: 4.71s
109:	learn: 36611.7293989	test: 39685.7960838	best: 39685.7960838 (109)	total: 583ms	remaining: 4.72s
110:	learn: 36605.2736157	test: 39684.1459111	best: 39684.1459111 (110)	total: 589ms	remaining: 4.71s
111:	learn: 36584.7594535	test: 39677.7297214	best: 39677.7297214 (111)	total: 595ms	remaining: 4.72s
112:	learn: 36559.1957319	test: 39665.5766672	best: 39665.5766672 (112)	total: 600ms	remaining: 4.71s
113:	learn: 36557.7748731	test: 39665.7430977	best: 39665.5766672 (112)	total: 605ms	remaining: 4.7s
114:	learn: 36505.8313737	test: 39619.6856667	best: 39619.6856667 (114)	total: 610ms	r

206:	learn: 35810.0795770	test: 39293.9593754	best: 39293.9593754 (206)	total: 1.1s	remaining: 4.22s
207:	learn: 35809.4290120	test: 39293.6099086	best: 39293.6099086 (207)	total: 1.11s	remaining: 4.21s
208:	learn: 35797.4972540	test: 39284.5280843	best: 39284.5280843 (208)	total: 1.11s	remaining: 4.22s
209:	learn: 35797.0981107	test: 39284.4607100	best: 39284.4607100 (209)	total: 1.12s	remaining: 4.23s
210:	learn: 35796.2767260	test: 39284.4110653	best: 39284.4110653 (210)	total: 1.13s	remaining: 4.22s
211:	learn: 35795.8184202	test: 39284.3866104	best: 39284.3866104 (211)	total: 1.14s	remaining: 4.22s
212:	learn: 35793.9341977	test: 39285.0372604	best: 39284.3866104 (211)	total: 1.14s	remaining: 4.21s
213:	learn: 35784.4129771	test: 39278.0591380	best: 39278.0591380 (213)	total: 1.14s	remaining: 4.21s
214:	learn: 35783.0484658	test: 39278.0172826	best: 39278.0172826 (214)	total: 1.15s	remaining: 4.2s
215:	learn: 35781.8369701	test: 39276.9787368	best: 39276.9787368 (215)	total: 1.16s

302:	learn: 35210.1808361	test: 38971.8422877	best: 38970.9617135 (299)	total: 1.63s	remaining: 3.76s
303:	learn: 35209.3580735	test: 38971.3755239	best: 38970.9617135 (299)	total: 1.64s	remaining: 3.76s
304:	learn: 35207.9777921	test: 38970.7511527	best: 38970.7511527 (304)	total: 1.65s	remaining: 3.75s
305:	learn: 35184.8607862	test: 38947.5402057	best: 38947.5402057 (305)	total: 1.65s	remaining: 3.75s
306:	learn: 35184.3945081	test: 38947.7130882	best: 38947.5402057 (305)	total: 1.66s	remaining: 3.75s
307:	learn: 35177.1575250	test: 38948.0068522	best: 38947.5402057 (305)	total: 1.67s	remaining: 3.75s
308:	learn: 35174.7553485	test: 38947.4864026	best: 38947.4864026 (308)	total: 1.67s	remaining: 3.74s
309:	learn: 35167.9132513	test: 38943.8978422	best: 38943.8978422 (309)	total: 1.68s	remaining: 3.74s
310:	learn: 35162.7461301	test: 38942.0662347	best: 38942.0662347 (310)	total: 1.68s	remaining: 3.73s
311:	learn: 35158.4495428	test: 38939.8584657	best: 38939.8584657 (311)	total: 1.6

399:	learn: 34589.7888990	test: 38688.3702270	best: 38687.3573543 (396)	total: 2.18s	remaining: 3.27s
400:	learn: 34588.8106122	test: 38687.6127137	best: 38687.3573543 (396)	total: 2.18s	remaining: 3.26s
401:	learn: 34588.0347409	test: 38687.7243562	best: 38687.3573543 (396)	total: 2.19s	remaining: 3.26s
402:	learn: 34583.1995708	test: 38686.2471249	best: 38686.2471249 (402)	total: 2.2s	remaining: 3.25s
403:	learn: 34573.5224872	test: 38679.6838611	best: 38679.6838611 (403)	total: 2.2s	remaining: 3.25s
404:	learn: 34566.3982372	test: 38690.4630532	best: 38679.6838611 (403)	total: 2.21s	remaining: 3.24s
405:	learn: 34560.8704911	test: 38690.9627410	best: 38679.6838611 (403)	total: 2.21s	remaining: 3.23s
406:	learn: 34555.4516391	test: 38690.8122940	best: 38679.6838611 (403)	total: 2.22s	remaining: 3.23s
407:	learn: 34552.5906043	test: 38692.1563128	best: 38679.6838611 (403)	total: 2.22s	remaining: 3.22s
408:	learn: 34541.9615724	test: 38684.0469932	best: 38679.6838611 (403)	total: 2.23s

...

198:	learn: 33404.8457623	test: 39049.1867561	best: 39049.1867561 (198)	total: 1.02s	remaining: 4.12s
199:	learn: 33401.4684712	test: 39047.4272067	best: 39047.4272067 (199)	total: 1.03s	remaining: 4.12s
200:	learn: 33398.7535943	test: 39047.8785555	best: 39047.4272067 (199)	total: 1.03s	remaining: 4.11s
201:	learn: 33397.5042666	test: 39047.6972348	best: 39047.4272067 (199)	total: 1.04s	remaining: 4.11s
202:	learn: 33395.6706559	test: 39047.3989483	best: 39047.3989483 (202)	total: 1.05s	remaining: 4.11s
203:	learn: 33384.1176938	test: 39054.1950450	best: 39047.3989483 (202)	total: 1.05s	remaining: 4.1s
204:	learn: 33377.6473332	test: 39055.7127141	best: 39047.3989483 (202)	total: 1.06s	remaining: 4.1s
205:	learn: 33372.4292723	test: 39048.8079248	best: 39047.3989483 (202)	total: 1.06s	remaining: 4.09s
206:	learn: 33371.1225618	test: 39047.5475544	best: 39047.3989483 (202)	total: 1.07s	remaining: 4.09s
207:	learn: 33367.0234299	test: 39046.0241362	best: 39046.0241362 (207)	total: 1.07s

306:	learn: 32800.2091587	test: 38804.6801113	best: 38803.3824808 (304)	total: 1.57s	remaining: 3.55s
307:	learn: 32778.3019660	test: 38790.4550704	best: 38790.4550704 (307)	total: 1.58s	remaining: 3.55s
308:	learn: 32762.6051610	test: 38782.8729460	best: 38782.8729460 (308)	total: 1.59s	remaining: 3.55s
309:	learn: 32761.9149357	test: 38782.8199235	best: 38782.8199235 (309)	total: 1.59s	remaining: 3.54s
310:	learn: 32761.5096015	test: 38782.6937836	best: 38782.6937836 (310)	total: 1.6s	remaining: 3.54s
311:	learn: 32759.4748003	test: 38782.7620905	best: 38782.6937836 (310)	total: 1.6s	remaining: 3.54s
312:	learn: 32758.6519385	test: 38782.1264578	best: 38782.1264578 (312)	total: 1.61s	remaining: 3.53s
313:	learn: 32754.6734036	test: 38783.4799979	best: 38782.1264578 (312)	total: 1.61s	remaining: 3.52s
314:	learn: 32751.9521594	test: 38780.5661449	best: 38780.5661449 (314)	total: 1.62s	remaining: 3.52s
315:	learn: 32750.3100320	test: 38780.3885150	best: 38780.3885150 (315)	total: 1.62s

414:	learn: 32178.7517144	test: 38580.2605155	best: 38580.2605155 (414)	total: 2.13s	remaining: 3s
415:	learn: 32177.5799907	test: 38580.3065468	best: 38580.2605155 (414)	total: 2.13s	remaining: 2.99s
416:	learn: 32171.3464173	test: 38583.5541631	best: 38580.2605155 (414)	total: 2.14s	remaining: 2.99s
417:	learn: 32169.5605996	test: 38583.6542568	best: 38580.2605155 (414)	total: 2.14s	remaining: 2.98s
418:	learn: 32169.1070001	test: 38583.5611300	best: 38580.2605155 (414)	total: 2.15s	remaining: 2.98s
419:	learn: 32168.4973504	test: 38583.3317946	best: 38580.2605155 (414)	total: 2.15s	remaining: 2.98s
420:	learn: 32165.0526638	test: 38582.1845283	best: 38580.2605155 (414)	total: 2.16s	remaining: 2.97s
421:	learn: 32164.4934835	test: 38581.8367669	best: 38580.2605155 (414)	total: 2.16s	remaining: 2.96s
422:	learn: 32163.7767951	test: 38581.4949094	best: 38580.2605155 (414)	total: 2.17s	remaining: 2.96s
423:	learn: 32159.0265834	test: 38580.2723206	best: 38580.2605155 (414)	total: 2.17s	

522:	learn: 31591.3109376	test: 38403.1890157	best: 38401.7472154 (514)	total: 2.68s	remaining: 2.44s
523:	learn: 31588.4311828	test: 38402.7091585	best: 38401.7472154 (514)	total: 2.69s	remaining: 2.44s
524:	learn: 31571.5552444	test: 38397.1528093	best: 38397.1528093 (524)	total: 2.69s	remaining: 2.44s
525:	learn: 31571.2258252	test: 38397.2192279	best: 38397.1528093 (524)	total: 2.7s	remaining: 2.43s
526:	learn: 31569.7142995	test: 38396.1050091	best: 38396.1050091 (526)	total: 2.71s	remaining: 2.43s
527:	learn: 31561.1156166	test: 38395.7154714	best: 38395.7154714 (527)	total: 2.71s	remaining: 2.43s
528:	learn: 31559.9756218	test: 38395.3125864	best: 38395.3125864 (528)	total: 2.72s	remaining: 2.42s
529:	learn: 31558.8769363	test: 38395.7295676	best: 38395.3125864 (528)	total: 2.73s	remaining: 2.42s
530:	learn: 31545.6337392	test: 38395.2659025	best: 38395.2659025 (530)	total: 2.73s	remaining: 2.42s
531:	learn: 31543.8001473	test: 38394.8642612	best: 38394.8642612 (531)	total: 2.74

627:	learn: 31105.7135273	test: 38434.1518016	best: 38381.8119562 (607)	total: 3.24s	remaining: 1.92s
628:	learn: 31098.1972668	test: 38436.6639499	best: 38381.8119562 (607)	total: 3.24s	remaining: 1.91s
629:	learn: 31089.6780918	test: 38435.5715879	best: 38381.8119562 (607)	total: 3.25s	remaining: 1.91s
630:	learn: 31088.0292006	test: 38434.3212559	best: 38381.8119562 (607)	total: 3.26s	remaining: 1.9s
631:	learn: 31087.5719091	test: 38434.5415559	best: 38381.8119562 (607)	total: 3.27s	remaining: 1.9s
632:	learn: 31086.3894775	test: 38433.6037179	best: 38381.8119562 (607)	total: 3.27s	remaining: 1.9s
633:	learn: 31074.1688930	test: 38432.4128750	best: 38381.8119562 (607)	total: 3.27s	remaining: 1.89s
634:	learn: 31069.6728298	test: 38430.7650397	best: 38381.8119562 (607)	total: 3.28s	remaining: 1.89s
635:	learn: 31066.6373727	test: 38429.4028407	best: 38381.8119562 (607)	total: 3.29s	remaining: 1.88s
636:	learn: 31062.9974039	test: 38426.3841325	best: 38381.8119562 (607)	total: 3.29s	

In [64]:
print("Training Score: ",np.mean(train_score))
print("Test Score: ",np.mean(test_score))

Training Score:  31556.101537061943
Test Score:  34526.33796931496


In [65]:
predictions = pd.DataFrame(sub_list)

In [66]:
predictions.head(3)

0             1            2            3             4     \
0  61260.794807  30311.803443  3076.833784  4105.750389  35011.670937   
1  70153.946342  36491.508603  3733.258730  2139.846049  18207.246234   
2  65238.441124  29800.000745  2945.493854  3185.246231  25422.657799   

         5            6            7           8            9     ...  \
0  814.261365  1227.663995  5976.291872   84.951782  1110.010829  ...   
1  648.200029  1333.433045  5977.853367   73.671698  1368.135595  ...   
2  629.193712  1124.921211  5207.237263  134.948626  1161.029512  ...   

         4009           4010         4011         4012        4013  \
0  129.797158  149024.874743  1662.534123  5705.348964   -7.555446   
1  121.001576  139924.120215  1222.022664  1361.984600  459.283353   
2  124.294881  136631.592845  3289.078417  1127.110413  106.422707   

           4014        4015          4016          4017          4018  
0  40285.840435  736.480943  78241.117185  45068.543702  46174.685475  
1  42830.758479  210.866869  73428.462144  45742.784545  56819.346236  
2  46257.623172  593.783934  72233.497069  31548.310127  40532.952281  

[3 rows x 4019 columns]

In [67]:
predictions1 = predictions.T

In [68]:
predictions1

0             1             2             3             4
0     61260.794807  70153.946342  65238.441124  69743.244058  59891.335135
1     30311.803443  36491.508603  29800.000745  29119.644082  33494.322847
2      3076.833784   3733.258730   2945.493854   2705.855976   3774.878539
3      4105.750389   2139.846049   3185.246231  15901.198476   1895.150814
4     35011.670937  18207.246234  25422.657799  21567.106455  15917.180305
...            ...           ...           ...           ...           ...
4014  40285.840435  42830.758479  46257.623172  43480.187179  42878.480923
4015    736.480943    210.866869    593.783934    614.310477    621.867127
4016  78241.117185  73428.462144  72233.497069  62884.644557  76461.288078
4017  45068.543702  45742.784545  31548.310127  41941.054636  40724.556375
4018  46174.685475  56819.346236  40532.952281  83366.050901  49660.315389

[4019 rows x 5 columns]

In [76]:
sub_df = pd.DataFrame(predictions1.mean(axis=1))

In [77]:
sub_df

0
0     65257.552293
1     31843.455944
2      3247.264177
3      5445.438392
4     23225.172346
...            ...
4014  43146.578038
4015    555.461870
4016  72649.801807
4017  41005.049877
4018  55310.670056

[4019 rows x 1 columns]